## **1. Load Machine Learning Model**

In [1]:
import os
from machine_learning import FraudModel

path = os.getcwd()
path

'/Users/jeannetaoliviasantoso/streaming_processing'

## **2. Load Data Old Information From PostgreSQL** 

In [2]:
import json
import urllib.parse
import pandas as pd
from sqlalchemy import create_engine

# Load configuration from the JSON file
with open('producer/config.json', 'r') as config_file:
    config = json.load(config_file)

# Database connection details
db_config = config['database']
username = db_config['username']
password = db_config['password']
host = db_config['host']
port = db_config['port']
database = db_config['database']
password = urllib.parse.quote_plus(password)

# URL connection to PostgreSQL
db_url = f"postgresql://{username}:{password}@{host}:{port}/{database}"
engine = create_engine(db_url)

# Query the database and fetch data
df = pd.read_sql_query('SELECT * FROM old_information_jeanneta;', engine)

# Display the first 5 rows
print(df.head(5))


      nameOrig  oldbalanceOrg     nameDest  oldbalanceDest
0  C1231006815       170136.0  M1979787155             0.0
1  C1666544295        21249.0  M2044282225             0.0
2  C1305486145          181.0   C553264065             0.0
3   C840083671          181.0    C38997010         21182.0
4  C2048537720        41554.0  M1230701703             0.0


## **3. Build Connection MongoDB**

In [3]:
# pip install pymongo


In [4]:
import json
from pymongo import MongoClient

# Load configuration from the JSON file
with open('producer/config.json', 'r') as config_file:
    config = json.load(config_file)

# MongoDB connection details
mongodb_config = config['mongodb']
mongo_uri = mongodb_config['uri']
mongo_db = mongodb_config['db']

try:
    # Connect to MongoDB using the loaded URI
    client = MongoClient(mongo_uri)
    db = client[mongo_db]  # Select the database
    server_status = db.command("ping")
    print("MongoDB connection successful:", server_status)

    # List all databases
    databases = client.list_database_names()
    print("Databases:", databases)

except Exception as e:
    print("An error occurred:", e)


MongoDB connection successful: {'ok': 1.0}
Databases: ['admin', 'config', 'ftde02', 'ftde03', 'ftde3', 'local']


## **4. Load Data New Information From Kafka Producer**

In [5]:
# 1. Ambil Data dari Kafka Producer
# 2. Merge / Join dengan Data dari PostgreSQL
# 3. Prediksi Transaksi
# 4. Insert kedalam MongoDB

In [6]:
path

'/Users/jeannetaoliviasantoso/streaming_processing'

In [7]:
import json
from kafka import KafkaConsumer

if __name__ == "__main__":
    # Load Kafka configuration from JSON config
    with open('producer/config.json', 'r') as config_file:
        config = json.load(config_file)
    
    kafka_config = config['kafka']
    bootstrap_servers = kafka_config['bootstrap_servers']
    topic = kafka_config['topic']

    consumer = KafkaConsumer(topic, bootstrap_servers=bootstrap_servers)
    print("Starting the consumer")
    
    for msg in consumer:
        print(f"Records = {json.loads(msg.value)}")
        
        # Parsing pesan Kafka
        data = json.loads(msg.value)
        produder = pd.DataFrame([data])
        
        # Join old information di postgreSQL
        data = produder.merge(df, how='inner', on=['nameOrig','nameDest'])

        data_predict = data.drop(['nameOrig','nameDest'], axis=1)
        data_predict = data_predict.to_dict('index')[0]

        print(path)
        result = FraudModel.runModel(data_predict, path)
        data['predict'] = result
        
        # Insert MongoDB
        db = client["ftde3"]
        collection = db["fraud_jeanneta"]

        if isinstance(data.to_dict('index')[0], list):
            collection.insert_many(data.to_dict('index')[0])
        else:
            collection.insert_one(data.to_dict('index')[0])        
            print("Data telah disimpan ke MongoDB")


Starting the consumer
Records = {'step': 1, 'type': 'PAYMENT', 'amount': 2734.77, 'nameOrig': 'C1756207614', 'newbalanceOrig': 1776.23, 'nameDest': 'M1214133948', 'newbalanceDest': 0.0}
/Users/jeannetaoliviasantoso/streaming_processing


/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator OneHotEncoder from version 1.3.0 when using version 1.5.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScaler from version 1.3.0 when using version 1.5.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScale

Data telah disimpan ke MongoDB
Records = {'step': 1, 'type': 'CASH_OUT', 'amount': 102153.86, 'nameOrig': 'C2015301874', 'newbalanceOrig': 0.0, 'nameDest': 'C1335050193', 'newbalanceDest': 353532.56}
/Users/jeannetaoliviasantoso/streaming_processing


/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator OneHotEncoder from version 1.3.0 when using version 1.5.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScaler from version 1.3.0 when using version 1.5.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScale

Data telah disimpan ke MongoDB
Records = {'step': 1, 'type': 'PAYMENT', 'amount': 584.52, 'nameOrig': 'C712627377', 'newbalanceOrig': 14894.48, 'nameDest': 'M782228073', 'newbalanceDest': 0.0}
/Users/jeannetaoliviasantoso/streaming_processing


...

/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator OneHotEncoder from version 1.3.0 when using version 1.5.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScaler from version 1.3.0 when using version 1.5.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScale

Data telah disimpan ke MongoDB
Records = {'step': 1, 'type': 'PAYMENT', 'amount': 5029.67, 'nameOrig': 'C1349872758', 'newbalanceOrig': 0.0, 'nameDest': 'M950729555', 'newbalanceDest': 0.0}
/Users/jeannetaoliviasantoso/streaming_processing


/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator OneHotEncoder from version 1.3.0 when using version 1.5.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScaler from version 1.3.0 when using version 1.5.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/Users/jeannetaoliviasantoso/anaconda3/lib/python3.12/site-packages/sklearn/base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScale

Data telah disimpan ke MongoDB


KeyboardInterrupt: 